In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch import Tensor
import torch.nn.functional as F
from torch.optim.lr_scheduler import MultiStepLR
from torch.utils.tensorboard import SummaryWriter

In [2]:
# Convolutional neural network (two convolutional layers)
class GRU(nn.Module):
    def __init__(self, num_classes=4):
        super(GRU, self).__init__()
           
        self.d1 = nn.Dropout(p=0.25)      
        self.bn1 = nn.BatchNorm1d(64,affine=False)
        self.ac1 = nn.Softplus()
        #self.rnn = nn.RNN(64,256,dropout=0.25)
        self.gru = nn.GRU(64,256,dropout=0.25)
        self.fc1 = nn.Linear(256, 64)
        self.fc2 = nn.Linear(64, num_classes)
        
    def forward(self, x):      
        x, _= self.gru(x)
        #print(x.shape)
        x = x[:,-1,:]
        #print(x.shape)
        x = self.fc1(x)
        x = self.bn1(x)
        x = self.ac1(x)
        x = self.d1(x)
        x = self.fc2(x)

        return x

In [3]:
rnn = GRU(4)
input = torch.randn(10, 64, 64)
output= rnn(input)
print(output.shape)

torch.Size([10, 4])


C:\Users\murray\anaconda3\envs\pytorchEEG\lib\site-packages\torch\nn\modules\rnn.py:62: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.25 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "


In [4]:
writer = SummaryWriter()

In [5]:
train_set = pd.read_csv("data/final_format/train_set.csv",header=None).to_numpy()
train_label = pd.read_csv("data/final_format/train_label.csv",header=None).to_numpy()
test_set = pd.read_csv("data/final_format/test_set.csv",header=None).to_numpy()
test_label = pd.read_csv("data/final_format/test_label.csv",header=None).to_numpy()

In [6]:
#delet first row data
train_set = train_set[1:]
train_label = train_label[1:]
test_set = test_set[1:]
test_label = test_label[1:]
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392, 1) (3598, 4096) (3598, 1)


In [7]:
train_label = train_label.reshape(-1)
test_label = test_label.reshape(-1)
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 4096) (14392,) (3598, 4096) (3598,)


In [8]:
#transpose to set data in time sequence
train_set = train_set.reshape(-1,64,64)
train_set = np.transpose(train_set,[0,2,1])
test_set = test_set.reshape(-1,64,64)
test_set = np.transpose(test_set,[0,2,1])
print(train_set.shape, train_label.shape, test_set.shape, test_label.shape)

(14392, 64, 64) (14392,) (3598, 64, 64) (3598,)


In [9]:
# Hyper parameters
num_epochs = 300
num_classes = 4
batch_size = 64
learning_rate = 1e-3

In [10]:
train_set_tensor = Tensor(train_set) 
train_label_tensor = Tensor(train_label).type(torch.LongTensor)

train_dataset = TensorDataset(train_set_tensor,train_label_tensor) 
train_loader = DataLoader(train_dataset, batch_size=batch_size) 

test_set_tensor = Tensor(test_set) 
test_label_tensor = Tensor(test_label).type(torch.LongTensor)

test_dataset = TensorDataset(test_set_tensor,test_label_tensor) 
test_loader = DataLoader(test_dataset, batch_size=batch_size) 

In [11]:
# Device configuration
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
device

device(type='cuda', index=0)

In [12]:
model = GRU(num_classes).to(device)

In [13]:
# Loss and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate, weight_decay=1e-3) 
#optimizer = torch.optim.Adam(model.parameters(), lr=learning_rate) 
milestones = [50,100,150,200,250]
milestones = [a * len(train_loader) for a in milestones]
scheduler = MultiStepLR(optimizer, milestones=milestones, gamma=0.5)

In [14]:
# Train the model
total_step = len(train_loader)
for epoch in range(num_epochs):
    correct=0
    total=0
    running_loss = 0
    for i, (X, Y) in enumerate(train_loader):
        X = X.to(device)
        Y = Y.to(device)
        
        
        # Forward pass
        outputs = model(X)
        loss = criterion(outputs, Y)
        
        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        #scheduler.step() 
        #print(scheduler.get_last_lr()[0])
      
        optimizer.step()
        scheduler.step() 
        #print(optimizer.param_groups[0]["lr"])
        
        _, predicted = outputs.max(1)
        total += Y.size(0)
        correct += predicted.eq(Y).sum().item()
        running_loss += loss.item()
        accu=100.*correct/total
        train_loss = running_loss/(i+1)
        print ('Epoch [{}/{}], Step [{}/{}], Training Accuracy: {:.4f}%, Training Loss: {:.4f}%'.format(epoch+1, num_epochs, i+1, total_step, accu, train_loss))
    
   
        #writer.add_scalar(f'train/accuracy', accu, epoch)
        #writer.add_scalar(f'train/loss', train_loss, epoch)
        writer.add_scalars(f'train/accuracy_loss', {
            'accuracy': accu,
            'loss': train_loss,
        }, epoch)
        

Epoch [1/300], Step [1/225], Training Accuracy: 21.8750%, Training Loss: 1.5921%
Epoch [1/300], Step [2/225], Training Accuracy: 22.6562%, Training Loss: 1.5427%
Epoch [1/300], Step [3/225], Training Accuracy: 24.4792%, Training Loss: 1.5082%
Epoch [1/300], Step [4/225], Training Accuracy: 26.1719%, Training Loss: 1.5040%
Epoch [1/300], Step [5/225], Training Accuracy: 27.5000%, Training Loss: 1.4888%
Epoch [1/300], Step [6/225], Training Accuracy: 26.5625%, Training Loss: 1.4873%
Epoch [1/300], Step [7/225], Training Accuracy: 26.7857%, Training Loss: 1.4919%
Epoch [1/300], Step [8/225], Training Accuracy: 26.9531%, Training Loss: 1.4917%
Epoch [1/300], Step [9/225], Training Accuracy: 27.6042%, Training Loss: 1.4818%
Epoch [1/300], Step [10/225], Training Accuracy: 26.5625%, Training Loss: 1.4875%
Epoch [1/300], Step [11/225], Training Accuracy: 26.8466%, Training Loss: 1.4794%
Epoch [1/300], Step [12/225], Training Accuracy: 26.4323%, Training Loss: 1.4775%
Epoch [1/300], Step [13/2

Epoch [1/300], Step [112/225], Training Accuracy: 27.6786%, Training Loss: 1.4117%
Epoch [1/300], Step [113/225], Training Accuracy: 27.6410%, Training Loss: 1.4120%
Epoch [1/300], Step [114/225], Training Accuracy: 27.7686%, Training Loss: 1.4112%
Epoch [1/300], Step [115/225], Training Accuracy: 27.7989%, Training Loss: 1.4109%
Epoch [1/300], Step [116/225], Training Accuracy: 27.7209%, Training Loss: 1.4111%
Epoch [1/300], Step [117/225], Training Accuracy: 27.7110%, Training Loss: 1.4109%
Epoch [1/300], Step [118/225], Training Accuracy: 27.6615%, Training Loss: 1.4109%
Epoch [1/300], Step [119/225], Training Accuracy: 27.6392%, Training Loss: 1.4106%
Epoch [1/300], Step [120/225], Training Accuracy: 27.6042%, Training Loss: 1.4105%
Epoch [1/300], Step [121/225], Training Accuracy: 27.5956%, Training Loss: 1.4106%
Epoch [1/300], Step [122/225], Training Accuracy: 27.6639%, Training Loss: 1.4101%
Epoch [1/300], Step [123/225], Training Accuracy: 27.7312%, Training Loss: 1.4096%
Epoc

Epoch [1/300], Step [212/225], Training Accuracy: 28.8989%, Training Loss: 1.3946%
Epoch [1/300], Step [213/225], Training Accuracy: 28.9319%, Training Loss: 1.3945%
Epoch [1/300], Step [214/225], Training Accuracy: 28.9501%, Training Loss: 1.3942%
Epoch [1/300], Step [215/225], Training Accuracy: 28.9680%, Training Loss: 1.3940%
Epoch [1/300], Step [216/225], Training Accuracy: 28.9714%, Training Loss: 1.3937%
Epoch [1/300], Step [217/225], Training Accuracy: 29.0035%, Training Loss: 1.3932%
Epoch [1/300], Step [218/225], Training Accuracy: 28.9564%, Training Loss: 1.3937%
Epoch [1/300], Step [219/225], Training Accuracy: 28.9812%, Training Loss: 1.3932%
Epoch [1/300], Step [220/225], Training Accuracy: 28.9915%, Training Loss: 1.3927%
Epoch [1/300], Step [221/225], Training Accuracy: 29.0088%, Training Loss: 1.3927%
Epoch [1/300], Step [222/225], Training Accuracy: 28.9907%, Training Loss: 1.3928%
Epoch [1/300], Step [223/225], Training Accuracy: 29.0078%, Training Loss: 1.3928%
Epoc

Epoch [2/300], Step [87/225], Training Accuracy: 31.9325%, Training Loss: 1.3501%
Epoch [2/300], Step [88/225], Training Accuracy: 31.8892%, Training Loss: 1.3507%
Epoch [2/300], Step [89/225], Training Accuracy: 32.0049%, Training Loss: 1.3501%
Epoch [2/300], Step [90/225], Training Accuracy: 32.1181%, Training Loss: 1.3491%
Epoch [2/300], Step [91/225], Training Accuracy: 32.2115%, Training Loss: 1.3485%
Epoch [2/300], Step [92/225], Training Accuracy: 32.1671%, Training Loss: 1.3487%
Epoch [2/300], Step [93/225], Training Accuracy: 32.1405%, Training Loss: 1.3488%
Epoch [2/300], Step [94/225], Training Accuracy: 32.0977%, Training Loss: 1.3486%
Epoch [2/300], Step [95/225], Training Accuracy: 32.0395%, Training Loss: 1.3491%
Epoch [2/300], Step [96/225], Training Accuracy: 31.9661%, Training Loss: 1.3499%
Epoch [2/300], Step [97/225], Training Accuracy: 32.0071%, Training Loss: 1.3500%
Epoch [2/300], Step [98/225], Training Accuracy: 32.0631%, Training Loss: 1.3494%
Epoch [2/300], S

Epoch [2/300], Step [186/225], Training Accuracy: 32.0817%, Training Loss: 1.3479%
Epoch [2/300], Step [187/225], Training Accuracy: 32.1190%, Training Loss: 1.3477%
Epoch [2/300], Step [188/225], Training Accuracy: 32.1144%, Training Loss: 1.3478%
Epoch [2/300], Step [189/225], Training Accuracy: 32.1842%, Training Loss: 1.3473%
Epoch [2/300], Step [190/225], Training Accuracy: 32.1957%, Training Loss: 1.3470%
Epoch [2/300], Step [191/225], Training Accuracy: 32.1826%, Training Loss: 1.3470%
Epoch [2/300], Step [192/225], Training Accuracy: 32.1696%, Training Loss: 1.3470%
Epoch [2/300], Step [193/225], Training Accuracy: 32.1324%, Training Loss: 1.3470%
Epoch [2/300], Step [194/225], Training Accuracy: 32.2165%, Training Loss: 1.3462%
Epoch [2/300], Step [195/225], Training Accuracy: 32.2276%, Training Loss: 1.3465%
Epoch [2/300], Step [196/225], Training Accuracy: 32.2305%, Training Loss: 1.3466%
Epoch [2/300], Step [197/225], Training Accuracy: 32.2414%, Training Loss: 1.3467%
Epoc

...

Epoch [298/300], Step [167/225], Training Accuracy: 99.6257%, Training Loss: 0.0205%
Epoch [298/300], Step [168/225], Training Accuracy: 99.6280%, Training Loss: 0.0205%
Epoch [298/300], Step [169/225], Training Accuracy: 99.6302%, Training Loss: 0.0204%
Epoch [298/300], Step [170/225], Training Accuracy: 99.6140%, Training Loss: 0.0207%
Epoch [298/300], Step [171/225], Training Accuracy: 99.6162%, Training Loss: 0.0207%
Epoch [298/300], Step [172/225], Training Accuracy: 99.6185%, Training Loss: 0.0206%
Epoch [298/300], Step [173/225], Training Accuracy: 99.6207%, Training Loss: 0.0205%
Epoch [298/300], Step [174/225], Training Accuracy: 99.6228%, Training Loss: 0.0205%
Epoch [298/300], Step [175/225], Training Accuracy: 99.6250%, Training Loss: 0.0205%
Epoch [298/300], Step [176/225], Training Accuracy: 99.6271%, Training Loss: 0.0205%
Epoch [298/300], Step [177/225], Training Accuracy: 99.6292%, Training Loss: 0.0205%
Epoch [298/300], Step [178/225], Training Accuracy: 99.6313%, Tra

Epoch [299/300], Step [66/225], Training Accuracy: 99.5502%, Training Loss: 0.0197%
Epoch [299/300], Step [67/225], Training Accuracy: 99.5103%, Training Loss: 0.0200%
Epoch [299/300], Step [68/225], Training Accuracy: 99.4715%, Training Loss: 0.0202%
Epoch [299/300], Step [69/225], Training Accuracy: 99.4792%, Training Loss: 0.0200%
Epoch [299/300], Step [70/225], Training Accuracy: 99.4866%, Training Loss: 0.0199%
Epoch [299/300], Step [71/225], Training Accuracy: 99.4938%, Training Loss: 0.0198%
Epoch [299/300], Step [72/225], Training Accuracy: 99.4792%, Training Loss: 0.0201%
Epoch [299/300], Step [73/225], Training Accuracy: 99.4863%, Training Loss: 0.0200%
Epoch [299/300], Step [74/225], Training Accuracy: 99.4932%, Training Loss: 0.0199%
Epoch [299/300], Step [75/225], Training Accuracy: 99.5000%, Training Loss: 0.0199%
Epoch [299/300], Step [76/225], Training Accuracy: 99.5066%, Training Loss: 0.0199%
Epoch [299/300], Step [77/225], Training Accuracy: 99.5130%, Training Loss: 

Epoch [299/300], Step [165/225], Training Accuracy: 99.5549%, Training Loss: 0.0205%
Epoch [299/300], Step [166/225], Training Accuracy: 99.5388%, Training Loss: 0.0207%
Epoch [299/300], Step [167/225], Training Accuracy: 99.5415%, Training Loss: 0.0206%
Epoch [299/300], Step [168/225], Training Accuracy: 99.5443%, Training Loss: 0.0207%
Epoch [299/300], Step [169/225], Training Accuracy: 99.5470%, Training Loss: 0.0206%
Epoch [299/300], Step [170/225], Training Accuracy: 99.5496%, Training Loss: 0.0206%
Epoch [299/300], Step [171/225], Training Accuracy: 99.5431%, Training Loss: 0.0206%
Epoch [299/300], Step [172/225], Training Accuracy: 99.5458%, Training Loss: 0.0206%
Epoch [299/300], Step [173/225], Training Accuracy: 99.5484%, Training Loss: 0.0205%
Epoch [299/300], Step [174/225], Training Accuracy: 99.5510%, Training Loss: 0.0205%
Epoch [299/300], Step [175/225], Training Accuracy: 99.5536%, Training Loss: 0.0205%
Epoch [299/300], Step [176/225], Training Accuracy: 99.5561%, Tra

Epoch [300/300], Step [38/225], Training Accuracy: 99.5066%, Training Loss: 0.0224%
Epoch [300/300], Step [39/225], Training Accuracy: 99.5192%, Training Loss: 0.0231%
Epoch [300/300], Step [40/225], Training Accuracy: 99.5312%, Training Loss: 0.0227%
Epoch [300/300], Step [41/225], Training Accuracy: 99.4665%, Training Loss: 0.0235%
Epoch [300/300], Step [42/225], Training Accuracy: 99.4420%, Training Loss: 0.0236%
Epoch [300/300], Step [43/225], Training Accuracy: 99.4549%, Training Loss: 0.0233%
Epoch [300/300], Step [44/225], Training Accuracy: 99.4673%, Training Loss: 0.0231%
Epoch [300/300], Step [45/225], Training Accuracy: 99.4444%, Training Loss: 0.0237%
Epoch [300/300], Step [46/225], Training Accuracy: 99.4226%, Training Loss: 0.0240%
Epoch [300/300], Step [47/225], Training Accuracy: 99.4348%, Training Loss: 0.0237%
Epoch [300/300], Step [48/225], Training Accuracy: 99.4466%, Training Loss: 0.0237%
Epoch [300/300], Step [49/225], Training Accuracy: 99.4579%, Training Loss: 

Epoch [300/300], Step [137/225], Training Accuracy: 99.5552%, Training Loss: 0.0220%
Epoch [300/300], Step [138/225], Training Accuracy: 99.5584%, Training Loss: 0.0219%
Epoch [300/300], Step [139/225], Training Accuracy: 99.5616%, Training Loss: 0.0218%
Epoch [300/300], Step [140/225], Training Accuracy: 99.5647%, Training Loss: 0.0218%
Epoch [300/300], Step [141/225], Training Accuracy: 99.5678%, Training Loss: 0.0217%
Epoch [300/300], Step [142/225], Training Accuracy: 99.5709%, Training Loss: 0.0217%
Epoch [300/300], Step [143/225], Training Accuracy: 99.5739%, Training Loss: 0.0216%
Epoch [300/300], Step [144/225], Training Accuracy: 99.5660%, Training Loss: 0.0217%
Epoch [300/300], Step [145/225], Training Accuracy: 99.5690%, Training Loss: 0.0216%
Epoch [300/300], Step [146/225], Training Accuracy: 99.5612%, Training Loss: 0.0217%
Epoch [300/300], Step [147/225], Training Accuracy: 99.5536%, Training Loss: 0.0218%
Epoch [300/300], Step [148/225], Training Accuracy: 99.5566%, Tra

In [15]:
from playsound import playsound
playsound(u"sound.mp3")

In [16]:
# Test the model
model.eval()  # eval mode (batchnorm uses moving mean/variance instead of mini-batch mean/variance)
with torch.no_grad():
    correct = 0
    total = 0
    for X, Y in test_loader:
        X = X.to(device)
        Y = Y.to(device)
        outputs = model(X)
        _, predicted = torch.max(outputs.data, 1)
        total += Y.size(0)
        correct += (predicted == Y).sum().item()

    print('Test Accuracy : {} %'.format(100 * correct / total))

# Save the model checkpoint
#torch.save(model.state_dict(), 'model.ckpt')

Test Accuracy : 34.15786548082268 %
